In [1]:
import pandas as pd

import time
import re
import numpy as np

from selenium import webdriver
from selenium.webdriver.common.by import By
from selenium.webdriver.support.ui import WebDriverWait
from selenium.webdriver.support import expected_conditions as EC
from selenium.webdriver.support.ui import Select

from webdriver_manager.chrome import ChromeDriverManager

/Users/prinzmagtulis/.pyenv/versions/3.10.0/lib/python3.10/site-packages/pandas/compat/__init__.py:124: UserWarning: Could not import the lzma module. Your installed Python is incomplete. Attempting to use lzma compression will result in a RuntimeError.
  warnings.warn(msg)


In [2]:
driver = webdriver.Chrome(ChromeDriverManager().install())



====== WebDriver manager ======
Could not get version for google-chrome with the any command: /Applications/Google\ Chrome.app/Contents/MacOS/Google\ Chrome --version
Current google-chrome version is UNKNOWN
Get LATEST chromedriver version for UNKNOWN google-chrome
Driver [/Users/prinzmagtulis/.wdm/drivers/chromedriver/mac64/96.0.4664.45/chromedriver] found in cache
/var/folders/01/dz49lpcd4qq_yksvf114xzfc0000gn/T/ipykernel_2069/1503906442.py:1: DeprecationWarning: executable_path has been deprecated, please pass in a Service object
  driver = webdriver.Chrome(ChromeDriverManager().install())


In [3]:
driver.get("https://www.officialgazette.gov.ph/past-sona-speeches/")

In [4]:
import requests
from bs4 import BeautifulSoup

In [5]:
rows= driver.find_elements(By.TAG_NAME, "tr")

In [6]:
dataset=[]
for dicts in rows[1:]:
    data={}
    all_tds = dicts.find_elements(By.TAG_NAME, "td")
    if len(all_tds) == 5:
        prexy = data['president']= dicts.find_elements(By.TAG_NAME, "td")[0].text
        data['date']= dicts.find_elements(By.TAG_NAME, "td")[1].text
        data['title'] = dicts.find_elements(By.TAG_NAME, "td")[2].text
        try:
            data['link'] = dicts.find_elements(By.TAG_NAME, "a")[1].get_attribute('href')
        except:
            data['link'] = dicts.find_element(By.TAG_NAME, "a").get_attribute('href')
        data['venue'] = dicts.find_elements(By.TAG_NAME, "td")[3].text
        data['session'] = dicts.find_elements(By.TAG_NAME, "td")[4].text
        dataset.append(data)
    else:
        data['president'] = prexy
        data['date']= dicts.find_elements(By.TAG_NAME, "td")[0].text
        data['title'] = dicts.find_elements(By.TAG_NAME, "td")[1].text
        data['link'] = dicts.find_element(By.TAG_NAME, "a").get_attribute('href')
        data['venue'] = dicts.find_elements(By.TAG_NAME, "td")[2].text
        data['session'] = dicts.find_elements(By.TAG_NAME, "td")[3].text
        dataset.append(data)
dataset

[{'president': 'Manuel L. Quezon',
  'date': 'November 25, 1935',
  'title': 'Message to the First Assembly on National Defense',
  'link': 'http://www.officialgazette.gov.ph/1935/11/25/message-of-president-quezon-to-the-first-assembly-on-national-defense-november-25-1935/',
  'venue': 'Legislative Building, Manila',
  'session': 'First National Assembly, First Session'},
 {'president': 'Manuel L. Quezon',
  'date': 'June 16, 1936',
  'title': 'On the Country’s Conditions and Problems',
  'link': 'http://www.officialgazette.gov.ph/1936/06/16/manuel-l-quezon-second-state-of-the-nation-address-june-16-1936/',
  'venue': 'Legislative Building, Manila',
  'session': 'First National Assembly, First Session'},
 {'president': 'Manuel L. Quezon',
  'date': 'October 18, 1937',
  'title': 'Improvement of Philippine Conditions, Philippine Independence, and Relations with American High Commissioner',
  'link': 'http://www.officialgazette.gov.ph/1937/10/18/manuel-l-quezon-third-state-of-the-nation-

In [11]:
#data.keys()
#for one in dataset:
    #print(one["link"])

In [14]:
df1 = pd.DataFrame(dataset)
df1.head()

president               date  \
0  Manuel L. Quezon  November 25, 1935   
1  Manuel L. Quezon      June 16, 1936   
2  Manuel L. Quezon   October 18, 1937   
3  Manuel L. Quezon   January 24, 1938   
4  Manuel L. Quezon   January 24, 1939   

                                               title  \
0  Message to the First Assembly on National Defense   
1           On the Country’s Conditions and Problems   
2  Improvement of Philippine Conditions, Philippi...   
3                 Revision of the System of Taxation   
4  The State of the Nation and Important Economic...   

                                                link  \
0  http://www.officialgazette.gov.ph/1935/11/25/m...   
1  http://www.officialgazette.gov.ph/1936/06/16/m...   
2  http://www.officialgazette.gov.ph/1937/10/18/m...   
3  http://www.officialgazette.gov.ph/1938/01/24/m...   
4  http://www.officialgazette.gov.ph/1939/01/24/m...   

                          venue                                  session  
0  Legislative Building, Manila   First National Assembly, First Session  
1  Legislative Building, Manila   First National Assembly, First Session  
2  Legislative Building, Manila  First National Assembly, Second Session  
3  Legislative Building, Manila   First National Assembly, Third Session  
4  Legislative Building, Manila  Second National Assembly, First Session

In [13]:
speeches=[]
for speech in dataset[0:]:
    href = speech['link']
    raw_html = requests.get(href).content
    doc = BeautifulSoup(raw_html, "html.parser")
    headers = doc.find_all(class_= 'large-9 large-centered columns')[1]
    text={}
    text['link']= speech['link']
    text['speech']= headers.text 
    speeches.append(text)
speeches

[{'link': 'http://www.officialgazette.gov.ph/1935/11/25/message-of-president-quezon-to-the-first-assembly-on-national-defense-november-25-1935/',
  'speech': '\nMessage\nof\nHis Excellency Manuel L. Quezon \nPresident of the Philippines\nTo the First National Assembly on National Defense\n[Delivered in the Assembly Hall, Legislative Building on November 25, 1935]\nMr. Speaker, gentlemen of the National Assembly:\nAs I appear before you for the first time, allow me to extend to you my cordial greetings and congratulations upon your election to this august body. It is your unique privilege to serve our country at the most critical period of its existence—at a time when the course of its destiny will be charted.\nThe framers of our Constitution conferred upon our Government all the power and authority needed to meet the demands of a progressive and enlightened epoch so that it may be able to promote the welfare and happiness of our people and safeguard their liberty.\nI know you are well 

In [17]:
df2=pd.DataFrame(speeches)
df2

link  \
0   http://www.officialgazette.gov.ph/1935/11/25/m...   
1   http://www.officialgazette.gov.ph/1936/06/16/m...   
2   http://www.officialgazette.gov.ph/1937/10/18/m...   
3   http://www.officialgazette.gov.ph/1938/01/24/m...   
4   http://www.officialgazette.gov.ph/1939/01/24/m...   
5   http://www.officialgazette.gov.ph/1940/01/22/m...   
6   http://www.officialgazette.gov.ph/1941/01/31/m...   
7   http://www.officialgazette.gov.ph/1945/06/09/s...   
8   http://www.officialgazette.gov.ph/1946/06/03/m...   
9   http://www.officialgazette.gov.ph/1947/01/27/m...   
10  http://www.officialgazette.gov.ph/1948/01/26/m...   
11  http://www.officialgazette.gov.ph/1949/01/24/e...   
12  http://www.officialgazette.gov.ph/1950/01/23/e...   
13  http://www.officialgazette.gov.ph/1951/01/22/e...   
14  http://www.officialgazette.gov.ph/1952/01/28/e...   
15  http://www.officialgazette.gov.ph/1953/01/26/e...   
16  http://www.officialgazette.gov.ph/1954/01/25/r...   
17  http://www.officialgazette.gov.ph/1955/01/24/r...   
18  http://www.officialgazette.gov.ph/1956/01/23/r...   
19  http://www.officialgazette.gov.ph/1957/01/28/r...   
20  http://www.officialgazette.gov.ph/1958/01/27/c...   
21  http://www.officialgazette.gov.ph/1959/01/26/c...   
22  http://www.officialgazette.gov.ph/1960/01/25/c...   
23  http://www.officialgazette.gov.ph/1961/01/23/c...   
24  http://www.officialgazette.gov.ph/1962/01/22/d...   
25  http://www.officialgazette.gov.ph/1963/01/28/d...   
26  http://www.officialgazette.gov.ph/1964/01/27/d...   
27  http://www.officialgazette.gov.ph/1965/01/25/d...   
28  http://www.officialgazette.gov.ph/1966/01/24/f...   
29  http://www.officialgazette.gov.ph/1967/01/23/f...   
30  http://www.officialgazette.gov.ph/1968/01/22/f...   
31  http://www.officialgazette.gov.ph/1969/01/27/f...   
32  http://www.officialgazette.gov.ph/1970/01/26/f...   
33  http://www.officialgazette.gov.ph/1971/01/25/f...   
34  http://www.officialgazette.gov.ph/1972/01/24/f...   
35  http://www.officialgazette.gov.ph/1973/09/21/f...   
36  http://www.officialgazette.gov.ph/1974/09/21/f...   
37  http://www.officialgazette.gov.ph/1975/09/19/f...   
38  http://www.officialgazette.gov.ph/1976/09/21/f...   
39  http://www.officialgazette.gov.ph/1977/09/21/f...   
40  http://www.officialgazette.gov.ph/1978/06/12/f...   
41  http://www.officialgazette.gov.ph/1979/07/23/f...   
42  http://www.officialgazette.gov.ph/1980/07/28/f...   
43  http://www.officialgazette.gov.ph/1981/07/27/f...   
44  http://www.officialgazette.gov.ph/1982/07/26/f...   
45  http://www.officialgazette.gov.ph/1983/01/17/f...   
46  http://www.officialgazette.gov.ph/1984/07/23/f...   
47  http://www.officialgazette.gov.ph/1985/07/22/f...   
48  http://www.officialgazette.gov.ph/1987/07/27/c...   
49  http://www.officialgazette.gov.ph/1988/07/25/c...   
50  http://www.officialgazette.gov.ph/1989/07/24/c...   
51  http://www.officialgazette.gov.ph/1990/07/23/c...   
52  http://www.officialgazette.gov.ph/1991/07/22/c...   
53  http://www.officialgazette.gov.ph/1992/07/27/f...   
54  http://www.officialgazette.gov.ph/1993/07/26/f...   
55  http://www.officialgazette.gov.ph/1994/07/25/f...   
56  http://www.officialgazette.gov.ph/1995/07/24/f...   
57  http://www.officialgazette.gov.ph/1996/07/22/f...   
58  http://www.officialgazette.gov.ph/1997/07/28/f...   
59  http://www.officialgazette.gov.ph/1998/07/27/j...   
60  http://www.officialgazette.gov.ph/1999/07/26/j...   
61  http://www.officialgazette.gov.ph/2000/07/24/j...   
62  http://www.officialgazette.gov.ph/2001/07/23/g...   
63  http://www.officialgazette.gov.ph/2002/07/22/g...   
64  http://www.officialgazette.gov.ph/2003/07/28/g...   
65  http://www.officialgazette.gov.ph/2004/07/26/g...   
66  http://www.officialgazette.gov.ph/2005/07/25/g...   
67  http://www.officialgazette.gov.ph/2006/07/24/g...   
68  http://www.officialgazette.gov.ph/2007/07/23/g...   
69  http://www.officialgazette.gov.ph/2008/07/28/g...   
70

In [18]:
merged = df1.merge(df2, suffixes=('_left'))
merged

/Users/prinzmagtulis/.pyenv/versions/3.10.0/lib/python3.10/site-packages/pandas/core/frame.py:9190: FutureWarning: Passing 'suffixes' as a <class 'str'>, is not supported and may give unexpected results. Provide 'suffixes' as a tuple instead. In the future a 'TypeError' will be raised.
  return merge(


president                date  \
0          Manuel L. Quezon   November 25, 1935   
1          Manuel L. Quezon       June 16, 1936   
2          Manuel L. Quezon    October 18, 1937   
3          Manuel L. Quezon    January 24, 1938   
4          Manuel L. Quezon    January 24, 1939   
5          Manuel L. Quezon    January 22, 1940   
6          Manuel L. Quezon    January 31, 1941   
7             Sergio Osmeña        June 9, 1945   
8              Manuel Roxas        June 3, 1946   
9              Manuel Roxas    January 27, 1947   
10             Manuel Roxas    January 26, 1948   
11          Elpidio Quirino    January 24, 1949   
12          Elpidio Quirino    January 23, 1950   
13          Elpidio Quirino    January 22, 1951   
14          Elpidio Quirino    January 28, 1952   
15          Elpidio Quirino    January 26, 1953   
16          Ramon Magsaysay    January 25, 1954   
17          Ramon Magsaysay    January 24, 1955   
18          Ramon Magsaysay    January 23, 1956   
19          Ramon Magsaysay    January 28, 1957   
20         Carlos P. Garcia    January 27, 1958   
21         Carlos P. Garcia    January 26, 1959   
22         Carlos P. Garcia    January 25, 1960   
23         Carlos P. Garcia    January 23, 1961   
24       Diosdado Macapagal    January 22, 1962   
25       Diosdado Macapagal    January 28, 1963   
26       Diosdado Macapagal    January 27, 1964   
27       Diosdado Macapagal    January 25, 1965   
28      Ferdinand E. Marcos    January 24, 1966   
29      Ferdinand E. Marcos    January 23, 1967   
30      Ferdinand E. Marcos    January 22, 1968   
31      Ferdinand E. Marcos    January 27, 1969   
32      Ferdinand E. Marcos    January 26, 1970   
33      Ferdinand E. Marcos    January 25, 1971   
34      Ferdinand E. Marcos    January 24, 1972   
35      Ferdinand E. Marcos  September 21, 1973   
36      Ferdinand E. Marcos  September 21, 1974   
37      Ferdinand E. Marcos  September 19, 1975   
38      Ferdinand E. Marcos  September 21, 1976   
39      Ferdinand E. Marcos  September 21, 1977   
40      Ferdinand E. Marcos       June 12, 1978   
41      Ferdinand E. Marcos       July 23, 1979   
42      Ferdinand E. Marcos       July 28, 1980   
43      Ferdinand E. Marcos       July 27, 1981   
44      Ferdinand E. Marcos       July 26, 1982   
45      Ferdinand E. Marcos    January 17, 1983   
46      Ferdinand E. Marcos       July 23, 1984   
47      Ferdinand E. Marcos       July 22, 1985   
48        Corazon C. Aquino       July 27, 1987   
49        Corazon C. Aquino       July 25, 1988   
50        Corazon C. Aquino       July 24, 1989   
51        Corazon C. Aquino       July 23, 1990   
52        Corazon C. Aquino       July 22, 1991   
53           Fidel V. Ramos       July 27, 1992   
54           Fidel V. Ramos       July 26, 1993   
55           Fidel V. Ramos       July 25, 1994   
56           Fidel V. Ramos       July 24, 1995   
57           Fidel V. Ramos       July 22, 1996   
58           Fidel V. Ramos       July 28, 1997   
59  Joseph Ejercito Estrada       July 27, 1998   
60  Joseph Ejercito Estrada       July 26, 1999   
61  Joseph Ejercito Estrada       July 24, 2000   
62  Gloria Macapagal-Arroyo       July 23, 2001   
63  Gloria Macapagal-Arroyo       July 22, 2002   
64  Gloria Macapagal-Arroyo       July 28, 2003   
65  Gloria Macapagal-Arroyo       July 26, 2004   
66  Gloria Macapagal-Arroyo       July 25, 2005   
67  Gloria Macapagal-Arroyo       July 24, 2006   
68  Gloria Macapagal-Arroyo       July 23, 2007   
69  Gloria Macapagal-Arroyo       July 28, 2008   
70  Gloria Macapagal-Arroyo       July 27, 2009   
71    Benigno S. Aquino III       July 26, 2010   
72    Benigno S. Aquino III       July 25, 2011   
73    Benigno S. Aquino III       July 23, 2012   
74    Benigno S. Aquino III       July 22, 2013   
75    Benigno S. Aquino III       July 28, 2014   
76    Benigno S. Aquino III       July 27, 2015   
77      Rodrigo Roa Duterte       July 2

In [19]:
merged.dtypes

president    object
date         object
title        object
link         object
venue        object
session      object
speech       object
dtype: object

In [20]:
merged[merged.speech.str.contains(r"\belite", case=False, regex=True)].president.value_counts()

Ferdinand E. Marcos        2
Joseph Ejercito Estrada    1
Rodrigo Roa Duterte        1
Name: president, dtype: int64

In [25]:
merged.speech.str.extractall(r'(.*\belite.+)', re.IGNORECASE)

0
   match                                                   
31 0      It is fortunate that the nation will, just two...
37 0      Clearly, we face here the danger that our New ...
60 0      Our war on poverty is in the acceleration of t...
81 0      Great wealth enables economic elites and corpo...

In [36]:
#pd.set_option('display.max_rows', None)
merged.speech.str.extractall(r'(.*\bdemocracy.+)', re.IGNORECASE)#.value_counts()

0
   match                                                   
1  0      In our day and generation democracy, as an eff...
2  0      Still more: The Filipino workingman has heard,...
   1      One of the discoveries which we have made sinc...
   2      Gentlemen of the National Assembly, before clo...
3  0      We are earnestly concerned with social justice...
4  0      As a final word respecting the Army, I want to...
   1      Gentlemen of the National Assembly, the world ...
6  0      As this body is about to pass into history by ...
   1      As you already know, the people of the United ...
   2      Gentlemen of the National Assembly, these are ...
8  0      One answer to this, of course, is small busine...
   1      Another of our major problems is transport and...
   2      Nor can we afford to forget the urgency of reh...
9  0      We have preserved our birthright of freedom an...
   1      Our schools must continue to function in the t...
10 0      They will not succeed in our land. Their numbe...
11 0      Looking thus at the record since the establish...
13 0      The new year presages events of extremely seri...
14 0      You and I, regardless of party alignments, hav...
   1      We showed this in our last popular experiment....
   2      Simultaneously, we directed our attention to t...
16 0      Against this conspiracy we will continue our p...
   1      I am for the adoption of a public works progra...
   2      To guide us in the conduct of public business,...
   3      Perhaps you will say that the people are askin...
17 0      The pre-fabricated schoolhouses now being mass...
   1      This Administration has made every effort to s...
18 0      The establishment of barrio councils pursuant ...
   1      Our Government’s deep concern for the common m...
19 0      We cannot afford to falter in our social justi...
21 0      Without veering away from America, but rather ...
   1      Finally, the provision on the suspension of th...
22 0      Permit me gentlemen of congress, to reiterate ...
   1      6) Finally, the provision on the suspension of...
24 0      4. The establishment of practices that will st...
   1                                     Democracy on Trial
   2      In the accomplishment of our mission, we have ...
   3      By our success or failure in leading the Natio...
25 0      We reject the imputation that we seek the cont...
   1      Partisan conflict is perhaps unavoidable in a ...
   2      To those who promote their interest through ha...
   3      An over-all program to abolish tenancy, as wel...
   4      The Administration has accordingly maintained ...
   5      To strengthen our democracy and bolster the ef...
26 0      Without diminishing our historic relations wit...
27 0      The system of freedom—we have restored free en...
   1      We are a young and developing democracy in a r...
29 0      The epic is also being written by men young an...
   1      What is being written is the epic of developme...
   2      Sometimes, as in the case of the Retail Trade ...
   3      It would be insulting to our national dignity ...
   4      The failure of justice—the inability of the pe...
   5      There is, therefore, a real crisis in the judi...
   6      But we cannot succeed completely until we rega...
30 0      We have laid the basis for industrial democrac...
   1      This is one of the tragedies of our democracy....
31 0      The inefficiency and the immorality in governm...
   1      It is fortunate that the nation will, just two...
   2      We must aim at the reality rather than at the ...
   3      There are those among us who will oppose—proba...
32 0      In regard to our efforts in Central Luzon, mil...
33 0      I have come to you through the streets of Mani...
34 0      Once again the last election put the life of o...
   1      No matter which political party or candidates ...
   2      Thus, we see initial uncertainty and differenc...
   3      But the main challenge to de